In [16]:
import numpy as np
import pandas as pd
from sklearn.metrics import f1_score, average_precision_score
from sklearn.model_selection import StratifiedGroupKFold
from xgboost import XGBClassifier
from extinction import fitzpatrick99
from lightgbm import LGBMClassifier
import optuna

In [17]:
FILTERS = ["u", "g", "r", "i", "z", "y"]

EFF_WL_AA = {
    "u": 3641.0,
    "g": 4704.0,
    "r": 6155.0,
    "i": 7504.0,
    "z": 8695.0,
    "y": 10056.0,
}

R_V = 3.1
STETSON_DT_MAX = 0.5

In [18]:
def safe_float(x, default=np.nan):
    try:
        if x is None:
            return default
        x = float(x)
        if np.isnan(x):
            return default
        return x
    except Exception:
        return default


def trapz_safe(y, x):
    if hasattr(np, "trapezoid"):
        return np.trapezoid(y, x)
    y = np.asarray(y)
    x = np.asarray(x)
    return np.sum((x[1:] - x[:-1]) * (y[1:] + y[:-1]) * 0.5)


def median_abs_dev(x):
    x = np.asarray(x)
    med = np.median(x)
    return float(np.median(np.abs(x - med)))


def iqr(x):
    q75, q25 = np.percentile(x, [75, 25])
    return float(q75 - q25)


def skewness(x):
    x = np.asarray(x)
    mu = np.mean(x)
    s = np.std(x)
    if s < 1e-12:
        return 0.0
    m3 = np.mean((x - mu) ** 3)
    return float(m3 / (s ** 3))


def kurtosis_excess(x):
    x = np.asarray(x)
    mu = np.mean(x)
    s = np.std(x)
    if s < 1e-12:
        return 0.0
    m4 = np.mean((x - mu) ** 4)
    return float(m4 / (s ** 4) - 3.0)


def von_neumann_eta(x):
    x = np.asarray(x)
    n = len(x)
    if n < 3:
        return np.nan
    v = np.var(x)
    if v < 1e-12:
        return 0.0
    dif = np.diff(x)
    return float(np.mean(dif ** 2) / v)


def max_slope(t, f):
    t = np.asarray(t)
    f = np.asarray(f)
    if len(t) < 3:
        return np.nan
    dt = np.diff(t)
    df = np.diff(f)
    good = dt > 0
    if not np.any(good):
        return np.nan
    slopes = df[good] / dt[good]
    return float(np.max(np.abs(slopes)))


def median_abs_slope(t, f):
    t = np.asarray(t)
    f = np.asarray(f)
    if len(t) < 3:
        return np.nan
    dt = np.diff(t)
    df = np.diff(f)
    good = dt > 0
    if not np.any(good):
        return np.nan
    slopes = df[good] / dt[good]
    return float(np.median(np.abs(slopes)))


def linear_slope(t, f):
    t = np.asarray(t)
    f = np.asarray(f)
    if len(t) < 3:
        return np.nan
    try:
        a, b = np.polyfit(t, f, 1)
        return float(a)
    except Exception:
        return np.nan


def chi2_to_constant(f, ferr):
    f = np.asarray(f)
    ferr = np.asarray(ferr)
    n = len(f)
    if n < 3:
        return np.nan
    mu = np.median(f)
    denom = (ferr + 1e-8) ** 2
    chi2 = np.sum((f - mu) ** 2 / denom)
    dof = max(1, n - 1)
    return float(chi2 / dof)


def interp_flux_at_time(tb, fb, t0):
    # returns flux at t0 using linear interpolation
    tb = np.asarray(tb)
    fb = np.asarray(fb)
    if len(tb) < 2:
        return np.nan
    if (t0 < tb.min()) or (t0 > tb.max()):
        return np.nan
    return float(np.interp(t0, tb, fb))


def stetson_J(t, f, ferr, dt_max=STETSON_DT_MAX):
    """
    Simplified Stetson J:
    Pair consecutive observations that are close in time.
    delta_i = sqrt(n/(n-1)) * (f_i - mean_f) / err_i
    J = mean( sign(P_k)*sqrt(|P_k|) ) where P_k = delta_i * delta_j
    """
    t = np.asarray(t)
    f = np.asarray(f)
    ferr = np.asarray(ferr)

    n = len(t)
    if n < 4:
        return np.nan

    mu = np.mean(f)
    scale = np.sqrt(n / max(1, n - 1))
    delta = scale * (f - mu) / (ferr + 1e-8)

    pairs = []
    for i in range(n - 1):
        if (t[i + 1] - t[i]) <= dt_max:
            pairs.append((i, i + 1))

    if len(pairs) == 0:
        return np.nan

    vals = []
    for i, j in pairs:
        P = delta[i] * delta[j]
        vals.append(np.sign(P) * np.sqrt(np.abs(P)))

    return float(np.mean(vals))


def fractional_variability(f, ferr):
    """
    Noise-corrected intrinsic variability amplitude:
    F_var = sqrt(max(0, S^2 - mean(err^2))) / |mean(f)|
    """
    f = np.asarray(f, float)
    ferr = np.asarray(ferr, float)
    n = len(f)
    if n < 3:
        return np.nan

    mu = np.mean(f)
    if np.abs(mu) < 1e-8:
        return np.nan

    s2 = np.var(f, ddof=1)
    mean_err2 = np.mean(ferr**2)

    excess = max(0.0, s2 - mean_err2)
    return float(np.sqrt(excess) / np.abs(mu))


def deextinct_band(flux, flux_err, ebv, band, r_v=R_V):
    if ebv is None or (isinstance(ebv, float) and np.isnan(ebv)):
        return flux, flux_err, 0.0

    A_V = float(ebv) * float(r_v)
    wave = np.array([EFF_WL_AA[band]], dtype=float)  # Angstrom
    A_lambda = float(fitzpatrick99(wave, A_V, r_v=r_v, unit="aa")[0])  # mag

    fac = 10.0 ** (0.4 * A_lambda)
    return flux * fac, flux_err * fac, A_lambda


def deextinct_lightcurve(lc, ebv):
    flux = lc["Flux"].to_numpy().astype(float)
    ferr = lc["Flux_err"].to_numpy().astype(float)
    filt = lc["Filter"].to_numpy()

    flux_corr = flux.copy()
    ferr_corr = ferr.copy()

    for b in FILTERS:
        m = (filt == b)
        if not np.any(m):
            continue
        flux_corr[m], ferr_corr[m], _ = deextinct_band(flux_corr[m], ferr_corr[m], ebv, b)

    return flux_corr, ferr_corr

def extract_features_for_object(lc_raw, z, z_err, ebv):
    feats = {}

    lc = lc_raw.sort_values("Time (MJD)").reset_index(drop=True)

    t = lc["Time (MJD)"].to_numpy().astype(float)
    filt = lc["Filter"].to_numpy()

    if len(t) == 0:
        feats["n_obs"] = 0
        return feats

    z = safe_float(z, default=0.0)
    z_err = safe_float(z_err, default=0.0)
    ebv = safe_float(ebv, default=np.nan)

    t_rel = t - t.min()
    t_rest = t_rel / (1.0 + z)
    flux_corr, err_corr = deextinct_lightcurve(lc, ebv)

    feats["n_obs"] = int(len(t))
    feats["total_time_obs"] = float(t_rel.max() - t_rel.min())
    feats["total_time_rest"] = float(t_rest.max() - t_rest.min())

    feats["flux_mean"] = float(np.mean(flux_corr))
    feats["flux_median"] = float(np.median(flux_corr))
    feats["flux_std"] = float(np.std(flux_corr))
    feats["flux_min"] = float(np.min(flux_corr))
    feats["flux_max"] = float(np.max(flux_corr))

    feats["flux_mad"] = median_abs_dev(flux_corr)
    feats["flux_iqr"] = iqr(flux_corr)
    feats["flux_skew"] = skewness(flux_corr)
    feats["flux_kurt_excess"] = kurtosis_excess(flux_corr)

    p5, p25, p75, p95 = np.percentile(flux_corr, [5, 25, 75, 95])
    feats["flux_p5"] = float(p5)
    feats["flux_p25"] = float(p25)
    feats["flux_p75"] = float(p75)
    feats["flux_p95"] = float(p95)
    feats["robust_amp_global"] = float(p95 - p5)

    feats["neg_flux_frac"] = float(np.mean(flux_corr < 0))

    snr = np.abs(flux_corr) / (err_corr + 1e-8)
    feats["snr_median"] = float(np.median(snr))
    feats["snr_max"] = float(np.max(snr))

    if len(t_rel) >= 2:
        dt = np.diff(t_rel)
        feats["median_dt"] = float(np.median(dt))
        feats["max_gap"] = float(np.max(dt))
    else:
        feats["median_dt"] = np.nan
        feats["max_gap"] = np.nan

    feats["eta_von_neumann"] = von_neumann_eta(flux_corr)
    feats["chi2_const_global"] = chi2_to_constant(flux_corr, err_corr)
    feats["stetsonJ_global_obs"] = stetson_J(t_rel, flux_corr, err_corr)
    feats["stetsonJ_global_rest"] = stetson_J(t_rest, flux_corr, err_corr)

    feats["max_slope_global_obs"] = max_slope(t_rel, flux_corr)
    feats["max_slope_global_rest"] = max_slope(t_rest, flux_corr)

    feats["med_abs_slope_global_obs"] = median_abs_slope(t_rel, flux_corr)
    feats["med_abs_slope_global_rest"] = median_abs_slope(t_rest, flux_corr)

    feats["slope_global_obs"] = linear_slope(t_rel, flux_corr)
    feats["slope_global_rest"] = linear_slope(t_rest, flux_corr)

    feats["fvar_global"] = fractional_variability(flux_corr, err_corr)

    feats["Z"] = float(z)
    feats["log1pZ"] = float(np.log1p(max(0.0, z)))
    feats["Z_err"] = float(max(0.0, z_err))
    feats["log1pZerr"] = float(np.log1p(max(0.0, feats["Z_err"])))
    feats["EBV"] = ebv

    feats["n_filters_present"] = 0
    feats["total_obs"] = 0

    band_amp = {}
    band_tpeak_rest = {}
    band_tpeak_obs = {}
    band_peak = {}

    band_tb_rest = {}
    band_tb_obs = {}
    band_fb = {}

    for b in FILTERS:
        m = (filt == b)
        nb = int(np.sum(m))
        feats[f"n_{b}"] = nb
        feats["total_obs"] += nb

        feats[f"amp_{b}"] = np.nan
        feats[f"robust_amp_{b}"] = np.nan

        feats[f"tpeak_{b}_obs"] = np.nan
        feats[f"tpeak_{b}_rest"] = np.nan

        feats[f"width50_{b}_obs"] = np.nan
        feats[f"width50_{b}_rest"] = np.nan
        feats[f"width80_{b}_obs"] = np.nan
        feats[f"width80_{b}_rest"] = np.nan

        feats[f"rise50_{b}_obs"] = np.nan
        feats[f"decay50_{b}_obs"] = np.nan
        feats[f"asym50_{b}_obs"] = np.nan

        feats[f"rise50_{b}_rest"] = np.nan
        feats[f"decay50_{b}_rest"] = np.nan
        feats[f"asym50_{b}_rest"] = np.nan

        feats[f"auc_pos_{b}_obs"] = np.nan
        feats[f"auc_pos_{b}_rest"] = np.nan

        feats[f"snrmax_{b}"] = np.nan
        feats[f"eta_{b}"] = np.nan
        feats[f"chi2_const_{b}"] = np.nan

        feats[f"slope_{b}_obs"] = np.nan
        feats[f"slope_{b}_rest"] = np.nan

        feats[f"maxslope_{b}_obs"] = np.nan
        feats[f"maxslope_{b}_rest"] = np.nan

        feats[f"stetsonJ_{b}_obs"] = np.nan
        feats[f"stetsonJ_{b}_rest"] = np.nan

        feats[f"p5_{b}"] = np.nan
        feats[f"p25_{b}"] = np.nan
        feats[f"p75_{b}"] = np.nan
        feats[f"p95_{b}"] = np.nan
        feats[f"mad_{b}"] = np.nan
        feats[f"iqr_{b}"] = np.nan
        feats[f"mad_over_std_{b}"] = np.nan

        feats[f"fvar_{b}"] = np.nan

        if nb == 0:
            continue
        feats["n_filters_present"] += 1

        tb_obs = t_rel[m]
        fb = flux_corr[m]
        eb = err_corr[m]

        order = np.argsort(tb_obs)
        tb_obs = tb_obs[order]
        fb = fb[order]
        eb = eb[order]

        tb_rest = tb_obs / (1.0 + z)

        baseline = float(np.median(fb))
        pidx = int(np.argmax(fb))
        peak_flux = float(fb[pidx])

        tpeak_obs = float(tb_obs[pidx])
        tpeak_rest = float(tb_rest[pidx])

        amp = peak_flux - baseline

        p5b, p25b, p75b, p95b = np.percentile(fb, [5, 25, 75, 95])
        feats[f"p5_{b}"] = float(p5b)
        feats[f"p25_{b}"] = float(p25b)
        feats[f"p75_{b}"] = float(p75b)
        feats[f"p95_{b}"] = float(p95b)
        feats[f"robust_amp_{b}"] = float(p95b - p5b)

        feats[f"mad_{b}"] = median_abs_dev(fb)
        feats[f"iqr_{b}"] = iqr(fb)
        stdb = float(np.std(fb))
        feats[f"mad_over_std_{b}"] = float(feats[f"mad_{b}"] / (stdb + 1e-8))

        feats[f"amp_{b}"] = float(amp)
        feats[f"tpeak_{b}_obs"] = tpeak_obs
        feats[f"tpeak_{b}_rest"] = tpeak_rest

        feats[f"snrmax_{b}"] = float(np.max(np.abs(fb) / (eb + 1e-8)))
        feats[f"eta_{b}"] = von_neumann_eta(fb)
        feats[f"chi2_const_{b}"] = chi2_to_constant(fb, eb)

        feats[f"slope_{b}_obs"] = linear_slope(tb_obs, fb)
        feats[f"slope_{b}_rest"] = linear_slope(tb_rest, fb)

        feats[f"maxslope_{b}_obs"] = max_slope(tb_obs, fb)
        feats[f"maxslope_{b}_rest"] = max_slope(tb_rest, fb)

        feats[f"stetsonJ_{b}_obs"] = stetson_J(tb_obs, fb, eb)
        feats[f"stetsonJ_{b}_rest"] = stetson_J(tb_rest, fb, eb)

        feats[f"fvar_{b}"] = fractional_variability(fb, eb)

        if nb >= 2:
            feats[f"auc_pos_{b}_obs"] = float(trapz_safe(np.maximum(fb - baseline, 0.0), tb_obs))
            feats[f"auc_pos_{b}_rest"] = float(trapz_safe(np.maximum(fb - baseline, 0.0), tb_rest))

        if (amp > 0) and (nb >= 3):
            lvl50 = baseline + 0.50 * amp
            lvl80 = baseline + 0.80 * amp

            def first_crossing_time(tt, ff, level, mode):
                if len(tt) < 2:
                    return np.nan
                if mode == "rise":
                    idx = np.where(ff >= level)[0]
                    return float(tt[idx[0]]) if len(idx) else np.nan
                if mode == "decay":
                    idx = np.where(ff <= level)[0]
                    return float(tt[idx[0]]) if len(idx) else np.nan
                return np.nan

            tb_rise_obs = tb_obs[:pidx + 1]
            fb_rise = fb[:pidx + 1]
            tb_dec_obs = tb_obs[pidx:]
            fb_dec = fb[pidx:]

            t_rise50_obs = first_crossing_time(tb_rise_obs, fb_rise, lvl50, "rise")
            t_fall50_obs = first_crossing_time(tb_dec_obs, fb_dec, lvl50, "decay")
            if (not np.isnan(t_rise50_obs)) and (not np.isnan(t_fall50_obs)):
                feats[f"width50_{b}_obs"] = float(t_fall50_obs - t_rise50_obs)
                feats[f"rise50_{b}_obs"] = float(tpeak_obs - t_rise50_obs)
                feats[f"decay50_{b}_obs"] = float(t_fall50_obs - tpeak_obs)
                feats[f"asym50_{b}_obs"] = float(feats[f"rise50_{b}_obs"] / (feats[f"decay50_{b}_obs"] + 1e-8))

            t_rise80_obs = first_crossing_time(tb_rise_obs, fb_rise, lvl80, "rise")
            t_fall80_obs = first_crossing_time(tb_dec_obs, fb_dec, lvl80, "decay")
            if (not np.isnan(t_rise80_obs)) and (not np.isnan(t_fall80_obs)):
                feats[f"width80_{b}_obs"] = float(t_fall80_obs - t_rise80_obs)

            tb_rise_rest = tb_rest[:pidx + 1]
            tb_dec_rest = tb_rest[pidx:]

            t_rise50_rest = first_crossing_time(tb_rise_rest, fb_rise, lvl50, "rise")
            t_fall50_rest = first_crossing_time(tb_dec_rest, fb_dec, lvl50, "decay")
            if (not np.isnan(t_rise50_rest)) and (not np.isnan(t_fall50_rest)):
                feats[f"width50_{b}_rest"] = float(t_fall50_rest - t_rise50_rest)
                feats[f"rise50_{b}_rest"] = float(tpeak_rest - t_rise50_rest)
                feats[f"decay50_{b}_rest"] = float(t_fall50_rest - tpeak_rest)
                feats[f"asym50_{b}_rest"] = float(feats[f"rise50_{b}_rest"] / (feats[f"decay50_{b}_rest"] + 1e-8))

            t_rise80_rest = first_crossing_time(tb_rise_rest, fb_rise, lvl80, "rise")
            t_fall80_rest = first_crossing_time(tb_dec_rest, fb_dec, lvl80, "decay")
            if (not np.isnan(t_rise80_rest)) and (not np.isnan(t_fall80_rest)):
                feats[f"width80_{b}_rest"] = float(t_fall80_rest - t_rise80_rest)

        band_amp[b] = feats[f"amp_{b}"]
        band_tpeak_obs[b] = feats[f"tpeak_{b}_obs"]
        band_tpeak_rest[b] = feats[f"tpeak_{b}_rest"]
        band_peak[b] = peak_flux

        band_tb_obs[b] = tb_obs
        band_tb_rest[b] = tb_rest
        band_fb[b] = fb

    pairs = [("u", "g"), ("g", "r"), ("r", "i"), ("i", "z"), ("z", "y")]
    for a, b in pairs:
        va, vb = band_amp.get(a, np.nan), band_amp.get(b, np.nan)
        ta_obs, tb_obs = band_tpeak_obs.get(a, np.nan), band_tpeak_obs.get(b, np.nan)
        ta_rest, tb_rest = band_tpeak_rest.get(a, np.nan), band_tpeak_rest.get(b, np.nan)
        pa, pb = band_peak.get(a, np.nan), band_peak.get(b, np.nan)

        feats[f"ampdiff_{a}{b}"] = (va - vb) if (not np.isnan(va) and not np.isnan(vb)) else np.nan
        feats[f"tpeakdiff_{a}{b}_obs"] = (ta_obs - tb_obs) if (not np.isnan(ta_obs) and not np.isnan(tb_obs)) else np.nan
        feats[f"tpeakdiff_{a}{b}_rest"] = (ta_rest - tb_rest) if (not np.isnan(ta_rest) and not np.isnan(tb_rest)) else np.nan
        feats[f"peakratio_{a}{b}"] = (pa / (pb + 1e-8)) if (not np.isnan(pa) and not np.isnan(pb)) else np.nan

    def logp(x):
        if np.isnan(x):
            return np.nan
        return float(np.log1p(max(0.0, x)))

    tpr_obs = feats.get("tpeak_r_obs", np.nan)
    if not np.isnan(tpr_obs):
        fr = interp_flux_at_time(band_tb_obs.get("r", np.array([])), band_fb.get("r", np.array([])), tpr_obs)
        fg = interp_flux_at_time(band_tb_obs.get("g", np.array([])), band_fb.get("g", np.array([])), tpr_obs)
        fi = interp_flux_at_time(band_tb_obs.get("i", np.array([])), band_fb.get("i", np.array([])), tpr_obs)

        feats["color_gr_at_rpeak_obs"] = (logp(fg) - logp(fr)) if (not np.isnan(fg) and not np.isnan(fr)) else np.nan
        feats["color_ri_at_rpeak_obs"] = (logp(fr) - logp(fi)) if (not np.isnan(fr) and not np.isnan(fi)) else np.nan

        dt_obs = 10.0
        t2 = tpr_obs + dt_obs

        fr2 = interp_flux_at_time(band_tb_obs.get("r", np.array([])), band_fb.get("r", np.array([])), t2)
        fg2 = interp_flux_at_time(band_tb_obs.get("g", np.array([])), band_fb.get("g", np.array([])), t2)
        fi2 = interp_flux_at_time(band_tb_obs.get("i", np.array([])), band_fb.get("i", np.array([])), t2)

        cgr1 = feats["color_gr_at_rpeak_obs"]
        cri1 = feats["color_ri_at_rpeak_obs"]

        cgr2 = (logp(fg2) - logp(fr2)) if (not np.isnan(fg2) and not np.isnan(fr2)) else np.nan
        cri2 = (logp(fr2) - logp(fi2)) if (not np.isnan(fr2) and not np.isnan(fi2)) else np.nan

        feats["color_gr_slope10_obs"] = ((cgr2 - cgr1) / dt_obs) if (not np.isnan(cgr2) and not np.isnan(cgr1)) else np.nan
        feats["color_ri_slope10_obs"] = ((cri2 - cri1) / dt_obs) if (not np.isnan(cri2) and not np.isnan(cri1)) else np.nan
    else:
        feats["color_gr_at_rpeak_obs"] = np.nan
        feats["color_ri_at_rpeak_obs"] = np.nan
        feats["color_gr_slope10_obs"] = np.nan
        feats["color_ri_slope10_obs"] = np.nan

    return feats

In [ ]:
def build_lightcurve_cache(splits, base_dir="data", kind="train"):
    lc_cache = {}
    idx_cache = {}

    for s in splits:
        path = f"{base_dir}/{s}/{kind}_full_lightcurves.csv"
        lc = pd.read_csv(path)
        groups = lc.groupby("object_id").indices
        lc_cache[s] = lc
        idx_cache[s] = groups

    return lc_cache, idx_cache


def get_lightcurve(lc_cache, idx_cache, split, object_id):
    idx = idx_cache[split].get(object_id, None)
    if idx is None:
        return None
    return lc_cache[split].iloc[idx]


def build_feature_table(
    log_df,
    lc_cache,
    idx_cache,
    augment_photoz=False,
    test_zerr_pool=None,
    n_aug=1,
    seed=6
):
    rng = np.random.default_rng(seed)
    rows = []

    if test_zerr_pool is not None:
        test_zerr_pool = np.asarray(test_zerr_pool, float)
        test_zerr_pool = test_zerr_pool[np.isfinite(test_zerr_pool)]
        test_zerr_pool = test_zerr_pool[test_zerr_pool > 0]

    for i in range(len(log_df)):
        r = log_df.iloc[i]
        obj = r["object_id"]
        split = r["split"]

        lc = get_lightcurve(lc_cache, idx_cache, split, obj)

        if lc is None:
            feats = {"n_obs": 0}
            feats["object_id"] = obj
            feats["split"] = split
            feats["photoz_aug"] = 0
            if "target" in log_df.columns:
                feats["target"] = int(r["target"])
            rows.append(feats)
            continue

        feats = extract_features_for_object(
            lc_raw=lc,
            z=r["Z"],
            z_err=r.get("Z_err", 0.0),
            ebv=r["EBV"],
        )
        feats["object_id"] = obj
        feats["split"] = split
        feats["photoz_aug"] = 0
        if "target" in log_df.columns:
            feats["target"] = int(r["target"])
        rows.append(feats)

        if augment_photoz and ("target" in log_df.columns) and (test_zerr_pool is not None) and (len(test_zerr_pool) > 0):
            z0 = safe_float(r["Z"], default=0.0)

            for _ in range(n_aug):
                sigma = float(rng.choice(test_zerr_pool))
                z_sim = max(0.0, z0 + float(rng.normal(0.0, sigma)))

                feats2 = extract_features_for_object(
                    lc_raw=lc,
                    z=z_sim,
                    z_err=sigma,
                    ebv=r["EBV"],
                )
                feats2["object_id"] = obj
                feats2["split"] = split
                feats2["target"] = int(r["target"])
                feats2["photoz_aug"] = 1
                rows.append(feats2)

    return pd.DataFrame(rows)

In [20]:
def clean_features(df, drop_cols):
    X = df.drop(columns=drop_cols).copy()

    X = X.replace([np.inf, -np.inf], np.nan)

    med = X.median(numeric_only=True)
    X = X.fillna(med)
    X = X.fillna(0.0)
    return X


def best_threshold_f1(y_true, probs):
    ths = np.linspace(0.01, 0.99, 200)
    f1s = [f1_score(y_true, probs > t, zero_division=0) for t in ths]
    j = int(np.argmax(f1s))
    return float(ths[j]), float(f1s[j])


def best_alpha_and_threshold(y_true, p_xgb, p_lgb):
    alphas = np.linspace(0.0, 1.0, 101)
    best = (0.5, 0.5, -1.0)  # alpha, th, f1

    for a in alphas:
        p = a * p_xgb + (1.0 - a) * p_lgb
        th, f1 = best_threshold_f1(y_true, p)
        if f1 > best[2]:
            best = (float(a), float(th), float(f1))

    return best


def make_splitter(n_splits, random_state=6):
    return StratifiedGroupKFold(n_splits=n_splits, shuffle=True, random_state=random_state)

In [ ]:
def run_optuna_xgb(train_feat, n_folds_tune=10, timeout_sec=7200):
    y = train_feat["target"].astype(int).to_numpy()
    groups = train_feat["split"].to_numpy()

    X = clean_features(train_feat, drop_cols=["object_id", "split", "target"])

    def objective(trial):
        params = {
            "objective": "binary:logistic",
            "eval_metric": "logloss",
            "random_state": 6,
            "n_jobs": -1,

            "tree_method": "hist",
            "device": "cuda",

            "n_estimators": trial.suggest_int("n_estimators", 600, 6000),
            "learning_rate": trial.suggest_float("learning_rate", 0.005, 0.12, log=True),

            "max_depth": trial.suggest_int("max_depth", 2, 10),
            "min_child_weight": trial.suggest_int("min_child_weight", 1, 40),

            "subsample": trial.suggest_float("subsample", 0.5, 1.0),
            "colsample_bytree": trial.suggest_float("colsample_bytree", 0.5, 1.0),

            "gamma": trial.suggest_float("gamma", 0.0, 10.0),
            "reg_alpha": trial.suggest_float("reg_alpha", 0.0, 20.0),
            "reg_lambda": trial.suggest_float("reg_lambda", 0.05, 30.0),

            "max_delta_step": trial.suggest_int("max_delta_step", 0, 10),

            "grow_policy": trial.suggest_categorical("grow_policy", ["depthwise", "lossguide"]),
        }

        if params["grow_policy"] == "lossguide":
            params["max_leaves"] = trial.suggest_int("max_leaves", 16, 256)

        scores = []

        splitter = make_splitter(n_folds_tune, random_state=6)
        split_iter = splitter.split(X, y, groups)

        for fold, (tr_idx, va_idx) in enumerate(split_iter, 1):
            X_tr, y_tr = X.iloc[tr_idx], y[tr_idx]
            X_va, y_va = X.iloc[va_idx], y[va_idx]

            neg = np.sum(y_tr == 0)
            pos = np.sum(y_tr == 1)
            params["scale_pos_weight"] = float(neg / max(1, pos))

            model = XGBClassifier(**params)
            model.fit(X_tr, y_tr, verbose=False)

            probs = model.predict_proba(X_va)[:, 1]
            ap = average_precision_score(y_va, probs)
            scores.append(ap)

            trial.report(float(np.mean(scores)), step=fold)
            if trial.should_prune():
                raise optuna.TrialPruned()

        return float(np.mean(scores))

    sampler = optuna.samplers.TPESampler(seed=6, multivariate=True, group=True)
    pruner = optuna.pruners.MedianPruner(n_startup_trials=30, n_warmup_steps=3)

    study = optuna.create_study(
        direction="maximize",
        sampler=sampler,
        pruner=pruner,
        study_name="xgb_ap_split_cv_gpu",
        storage="sqlite:///optuna_xgb_ap_gpu.db",
        load_if_exists=True
    )

    study.optimize(objective, n_trials=999999, timeout=timeout_sec)

    print("\nOptuna best AP:", study.best_value)
    print("Best params:")
    for k, v in study.best_params.items():
        print(k, "=", v)

    return study.best_params


In [22]:
def train_full_ensemble(train_feat, xgb_params, n_splits_full=20):
    y = train_feat["target"].astype(int).to_numpy()
    groups = train_feat["split"].to_numpy()

    X = clean_features(train_feat, drop_cols=["object_id", "split", "target"])

    splitter = make_splitter(n_splits_full, random_state=6)
    split_iter = splitter.split(X, y, groups)

    xgb_base = {
        "objective": "binary:logistic",
        "eval_metric": "logloss",
        "random_state": 6,
        "n_jobs": -1,
        "tree_method": "hist",
        "device": "cuda",
        **xgb_params
    }

    lgb_base = dict(
        objective="binary",
        boosting_type="gbdt",
        n_estimators=4000,
        learning_rate=0.02,
        num_leaves=64,
        max_depth=-1,
        min_child_samples=20,
        subsample=0.8,
        colsample_bytree=0.8,
        reg_alpha=0.0,
        reg_lambda=0.0,
        n_jobs=-1,
        random_state=6
    )

    xgb_models = []
    lgb_models = []

    oof_xgb = np.zeros(len(X), dtype=float)
    oof_lgb = np.zeros(len(X), dtype=float)

    for fold, (tr_idx, va_idx) in enumerate(split_iter, 1):
        X_tr, y_tr = X.iloc[tr_idx], y[tr_idx]
        X_va, y_va = X.iloc[va_idx], y[va_idx]

        neg = np.sum(y_tr == 0)
        pos = np.sum(y_tr == 1)
        spw = float(neg / max(1, pos))

        xgb_base["scale_pos_weight"] = spw
        xgb_model = XGBClassifier(**xgb_base)
        xgb_model.fit(X_tr, y_tr, verbose=False)
        p_xgb = xgb_model.predict_proba(X_va)[:, 1]
        oof_xgb[va_idx] = p_xgb
        xgb_models.append(xgb_model)

        lgb_model = LGBMClassifier(**{**lgb_base, "scale_pos_weight": spw})
        lgb_model.fit(X_tr, y_tr)
        p_lgb = lgb_model.predict_proba(X_va)[:, 1]
        oof_lgb[va_idx] = p_lgb
        lgb_models.append(lgb_model)

        p_tmp = 0.5 * p_xgb + 0.5 * p_lgb
        th, f1 = best_threshold_f1(y_va, p_tmp)
        print(f"Fold {fold:02d} | temp blend(0.5) best F1={f1:.4f} @ th={th:.3f}")

    alpha_best, th_best, f1_best = best_alpha_and_threshold(y, oof_xgb, oof_lgb)
    print("\nOOF best alpha:", alpha_best)
    print("OOF best threshold:", th_best)
    print("OOF blended best F1:", f1_best)

    return xgb_models, lgb_models, alpha_best, th_best


def predict_ensemble(test_feat, xgb_models, lgb_models, alpha):
    X_test = clean_features(test_feat, drop_cols=["object_id", "split"])

    p_xgb = np.mean([m.predict_proba(X_test)[:, 1] for m in xgb_models], axis=0)
    p_lgb = np.mean([m.predict_proba(X_test)[:, 1] for m in lgb_models], axis=0)

    p_blend = alpha * p_xgb + (1.0 - alpha) * p_lgb
    return p_blend

In [23]:
train_log = pd.read_csv("data/train_log.csv")
test_log = pd.read_csv("data/test_log.csv")

if "Z_err" not in train_log.columns:
    train_log["Z_err"] = 0.0
train_log["Z_err"] = train_log["Z_err"].fillna(0.0)

if "Z_err" not in test_log.columns:
    test_log["Z_err"] = 0.0
test_log["Z_err"] = test_log["Z_err"].fillna(0.0)

train_splits = sorted(train_log["split"].unique())
test_splits = sorted(test_log["split"].unique())

train_lc_cache, train_idx_cache = build_lightcurve_cache(train_splits, base_dir="data", kind="train")
test_lc_cache, test_idx_cache = build_lightcurve_cache(test_splits, base_dir="data", kind="test")
test_zerr_pool = test_log["Z_err"].dropna().values

In [24]:
train_feat = build_feature_table(
    train_log, train_lc_cache, train_idx_cache,
    augment_photoz=True,
    test_zerr_pool=test_zerr_pool,
    n_aug=1,
    seed=6
)

test_feat = build_feature_table(test_log, test_lc_cache, test_idx_cache)

print("train_feat:", train_feat.shape)
print("test_feat :", test_feat.shape)

train_feat: (6086, 272)
test_feat : (7135, 271)


In [25]:
best_xgb_params = run_optuna_xgb(train_feat, n_folds_tune=10, timeout_sec=7200)
xgb_models, lgb_models, alpha_best, best_th = train_full_ensemble(
    train_feat, best_xgb_params, n_splits_full=len(train_splits)
)

c:\Users\rowes\Documents\GitHub\2026-ML-Projects\.venv\Lib\site-packages\optuna\_experimental.py:33: ExperimentalWarning: Argument ``multivariate`` is an experimental feature. The interface can change in the future.
  optuna_warn(
c:\Users\rowes\Documents\GitHub\2026-ML-Projects\.venv\Lib\site-packages\optuna\_experimental.py:33: ExperimentalWarning: Argument ``group`` is an experimental feature. The interface can change in the future.
  optuna_warn(
[I 2026-01-22 22:04:29,751] A new study created in RDB with name: xgb_ap_split_cv_gpu
c:\Users\rowes\Documents\GitHub\2026-ML-Projects\.venv\Lib\site-packages\xgboost\core.py:774: UserWarning: [22:04:37] WARNING: C:\actions-runner\_work\xgboost\xgboost\src\common\error_msg.cc:62: Falling back to prediction using DMatrix due to mismatched devices. This might lead to higher memory usage and slower performance. XGBoost is running on: cuda:0, while the input data is on: cpu.
Potential solutions:
- Use a data structure that matches the device o


Optuna best AP: 0.528035337432086
Best params:
n_estimators = 4328
learning_rate = 0.007079630495604182
max_depth = 4
min_child_weight = 1
subsample = 0.5936362024881353
colsample_bytree = 0.9146736072473098
gamma = 0.6466321530023438
reg_alpha = 4.130135428812432
reg_lambda = 5.5649710878468825
max_delta_step = 1
grow_policy = depthwise
[LightGBM] [Info] Number of positive: 290, number of negative: 5472
[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.014475 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 63776
[LightGBM] [Info] Number of data points in the train set: 5762, number of used features: 257
[LightGBM] [Info] [binary:BoostFromScore]: pavg=0.050330 -> initscore=-2.937519
[LightGBM] [Info] Start training from score -2.937519
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warni

In [26]:
test_probs = predict_ensemble(test_feat, xgb_models, lgb_models, alpha=alpha_best)
test_pred = (test_probs > best_th).astype(int)

sub = pd.DataFrame({
    "object_id": test_feat["object_id"].values,
    "target": test_pred
})
sub.to_csv("XGB-LGBM.csv", index=False)